# Pre-requisites

## Why TEI
There are 2 **unsung** challenges with RAG at scale:
1. Getting the embeddings efficiently
1. Efficient ingestion into the vector DB

The issue with `1.` is that there are techniques but they are not widely *applied*. TEI solves a number of aspects:
- Token Based Dynamic Batching
- Using latest optimizations (Flash Attention, Candle and cuBLASLt)
- Fast loading with safetensors

The issue with `2.` is that it takes a bit of planning. We wont go much into that side of things here though.

## Start TEI Locally
Run [TEI](https://github.com/huggingface/text-embeddings-inference#docker), I have this running in a nvidia-docker container, but you can install as you like. Note that I ran this in a different terminal for monitoring and seperation. 

Note that as its running, its always going to pull the latest. Its at a very early stage at the time of writing. 

I chose [sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2](https://huggingface.co/sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2) based on the STS ar-ar performance on [mteb/leaderboard](https://huggingface.co/spaces/mteb/leaderboard), its the top performer and half the size of second place! TEI is fast, but this will make our life easier for storage and retrieval.

I use the `revision=refs/pr/8` because this has the pull request with [safetensors](https://github.com/huggingface/safetensors) which is required by TEI. Check out the [pull request](https://huggingface.co/sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2/discussions/8) if you want to use a different embedding model and it doesnt have safetensors.

In [ ]:
%%bash

# volume=$pwd/tei
# model=sentence-transformers/paraphrase-multilingual-minilm-l12-v2
# revision=refs/pr/8
# docker run \
#     --gpus all \
#     -p 8080:80 \
#     -v $volume:/data \
#     -v /home/ec2-user/.cache/huggingface/token:/root/.cache/huggingface/token \
#     --pull always \
#     ghcr.io/huggingface/text-embeddings-inference:latest \
#     --model-id $model \
#     --revision $revision \
#     --pooling mean \
#     --max-batch-tokens 65536

### Test Endpoint

In [ ]:
%%bash

# response_code=$(curl -s -o /dev/null -w "%{http_code}" 127.0.0.1:8080/embed \
#     -X POST \
#     -d '{"inputs":"What is Deep Learning?"}' \
#     -H 'Content-Type: application/json')

# if [ "$response_code" -eq 200 ]; then
#     echo "passed"
# else
#     echo "failed"
# fi

## Start TEI with Inference Endpoints
Another option is to run TEI on Inference Endpoints. Its cheap and fast. It took me less than 5 minutes to get it up and running!

Check here for a [guide](https://huggingface.co/blog/inference-endpoints-embeddings#3-deploy-embedding-model-as-inference-endpoint). Make sure to set these options in order:
1. Model Repository = transformers/paraphrase-multilingual-minilm-l12-v2
1. Name your endpoint
1. Choose a GPU
1. Advanced Configuration
    1. Task = Sentence Embeddings
    1. Revision (based on [this pull request for safetensors](https://huggingface.co/sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2/discussions/8) = a21e6630
    1. Container Type = Text Embeddings Inference
    
Set the other options as you prefer.

### Test Endpoint

In [1]:
import getpass
bearer_token = getpass.getpass(prompt='What is your BEARER TOKEN? Check your endpoint.')
API_URL = getpass.getpass(prompt='What is your API_URL?')

What is your BEARER TOKEN? Check your endpoint. ········
What is your API_URL? ········


In [2]:
# Constants
HEADERS = {
	"Authorization": f"Bearer {bearer_token}",
	"Content-Type": "application/json"
}
MAX_WORKERS = 512

In [3]:
import requests


def query(payload):
	response = requests.post(API_URL, headers=HEADERS, json=payload)
	return response.json()
	
output = query({
	"inputs": "This sound track was beautiful! It paints the senery in your mind so well I would recomend it even to people who hate vid. game music!",
})
print(f'{output[0][:5]}...')

[0.0047912598, -0.03164673, -0.018051147, -0.057739258, -0.04498291]...


# Imports

In [4]:
import asyncio
from pathlib import Path
import json
import time


from aiohttp import ClientSession, ClientTimeout
from tqdm.notebook import tqdm

In [5]:
proj_dir = Path.cwd().parent
print(proj_dir)

/home/ec2-user/arabic-wiki


# Config

In [6]:
files_in = list((proj_dir / 'data/processed/').glob('*.ndjson'))
folder_out = proj_dir / 'data/embedded/'

# Embed
## Strategy
TEI allows multiple concurrent requests, so its important that we dont waste the potential we have. I used the default `max-concurrent-requests` value of `512`, so I want to use that many `MAX_WORKERS`.

Im using an `async` way of making requests that uses `aiohttp` as well as a nice progress bar. 

Note that Im using `'truncate':True` as even with our `350` word split earlier, there are always exceptions. Its important that as this scales we have as few issues as possible when embedding. 

In [7]:
async def request(document, semaphore):
    # Semaphore guard
    async with semaphore:
        payload = {
            "inputs": document['content'],
            "truncate": True
        }
        
        timeout = ClientTimeout(total=10)  # Set a timeout for requests (10 seconds here)

        async with ClientSession(timeout=timeout, headers=HEADERS) as session:
            async with session.post(API_URL, json=payload) as resp:
                if resp.status != 200:
                    raise RuntimeError(await resp.text())
                result = await resp.json()
                
        document['embedding'] = result[0]  # Assuming the API's output can be directly assigned
        return document

async def main(documents):
    # Semaphore to limit concurrent requests. Adjust the number as needed.
    semaphore = asyncio.BoundedSemaphore(512)

    # Creating a list of tasks
    tasks = [request(document, semaphore) for document in documents]
    
    # Using tqdm to show progress. It's been integrated into the async loop.
    for f in tqdm(asyncio.as_completed(tasks), total=len(documents)):
        await f


In [11]:
start = time.perf_counter()
for i, file_in in tqdm(enumerate(files_in)):

    with open(file_in, 'r') as f:
        documents = [json.loads(line) for line in f]
        
    # Get embeddings
    await main(documents)
        
    # Make sure we got it all
    count = 0
    for document in documents:
        if document['embedding'] and len(document['embedding']) == 384:
            count += 1
    print(f'Batch {i+1}: Embeddings = {count} documents = {len(documents)}')

    # Write to file
    with open(folder_out/file_in.name, 'w', encoding='utf-8') as f:
        for document in documents:
            json_str = json.dumps(document, ensure_ascii=False)
            f.write(json_str + '\n')
print(time.perf_counter() - start)

0it [00:00, ?it/s]

  0%|          | 0/243068 [00:00<?, ?it/s]

Batch 1: Embeddings = 243068 documents = 243068


  0%|          | 0/104065 [00:00<?, ?it/s]

Batch 2: Embeddings = 104065 documents = 104065


...

Batch 21: Embeddings = 121849 documents = 121849


  0%|          | 0/147110 [00:00<?, ?it/s]

Batch 22: Embeddings = 147110 documents = 147110


  0%|          | 0/70322 [00:00<?, ?it/s]

Batch 23: Embeddings = 70322 documents = 70322
6250.827601939993


In [ ]:
documents[0]

Lets double check that we got all the embeddings we expected!

Great, we can see that they match.

Let's write our embeddings to file

# Next Steps
We need to import this into a vector db. 